In [1]:
import random
from src.feature_extraction.feature_extractor_utils import *
from src.model.utils.training_utils import *
import torch


In [2]:
RANDOM_SEED = 42
np.random.seed(RANDOM_SEED)
random.seed(RANDOM_SEED)
torch.manual_seed(RANDOM_SEED)

In [3]:
# Load settings from settings.json
settings = Settings()
settings.load_settings()

settings.method_list = ['ldgd']
settings.debug_mode = False


Patient: ['p05']


In [4]:
# Set up paths for data
paths = Paths(settings)
paths.load_device_paths()
paths.create_paths()

In [5]:
# Load or extract features
features_raw_df_dict = load_or_extract_features(settings, paths)

In [6]:
# Perform training with cross-validation or single fold

random_seed = 42
patient_id = 0
patient_file_name_base = list(features_raw_df_dict.keys())[1]
features_df = features_raw_df_dict[patient_file_name_base]

print(f"====== Subject {patient_id} ({patient_file_name_base.split('.')[0]}) ====== \n")
# Extract labels and features
y_one_hot, labels_array, unique_pids, patients_files, features_df, target_columns = get_labels(features_df,
                                                                                               settings)
if settings.cross_validation_mode in ['k-fold', 'order']:
    # Generate k-folds for cross-validation
    cv_mode = setup_cross_validation(settings.cross_validation_mode, num_folds=settings.num_fold,
                                     random_state=random_seed)
    folds = generate_folds(features_df, labels_array, cv_mode, n_splits=settings.num_fold)
    folds = list(folds)
else:  # Single train/test split
    folds = [(train_test_split(np.arange(len(labels_array)), test_size=0.2, stratify=labels_array))]
        
all_results = []
for latent_dim in [1, 2, 3, 5, 7, 10]:
    patient_id = patient_id + 1
    settings.ldgd_configs['latent_dim'] = latent_dim
    # settings.num_epochs_train = num_epochs_train
    results_logger = ResultList(method_list=settings.method_list, metric_list=settings.metric_list)

    results_logger.add_subject(unique_pids=patient_id, patients_files=patients_files, params=f'_latent_dim_{latent_dim}')
    paths.create_subject_paths(patients_files.split('.')[0]+f'_latent_dim_{latent_dim}')
        
    fold_results = {method: [] for method in settings.method_list}
    fold_report_results = {method: [] for method in settings.method_list}

    for fold_idx, (train_index, test_index) in enumerate(folds):
        paths.create_fold_path(fold_idx)

        # Select features and prepare the training and testing datasets
        features_matrix, selected_features, patients_ids, _ = get_selected_features(
            features_df=features_df.copy(), settings=settings, paths=paths,
            fold_idx=fold_idx, train_index=train_index, target_columns_drop=get_drop_columns(settings),
            num_important_features=settings.num_important_features)

        data_train, data_test = features_matrix[train_index], features_matrix[test_index]
        labels_train, labels_test = labels_array[train_index], labels_array[test_index]
        y_train, y_test = y_one_hot[train_index], y_one_hot[test_index]

        # Train and evaluate models for each specified method
        for method in settings.method_list:
            print(f"=========== Train Subject {patient_id} Fold {fold_idx + 1} Model {method} Latent dim {latent_dim} =========== \n")
            results, report_results = train_model(method,
                                                  data_train=data_train,
                                                  labels_train=labels_train,
                                                  data_test=data_test,
                                                  labels_test=labels_test,
                                                  settings=settings,
                                                  paths=paths,
                                                  y_train=y_train,
                                                  y_test=y_test,
                                                  selected_features=selected_features,
                                                  target_columns=target_columns)
            fold_results[method].append(results)
            fold_report_results[method].append(report_results)

        plt.close('all')
    
    # Aggregate the results for fold reports
    aggregated_results = aggregate_fold_report_results(fold_report_results)


    # Save or print the DataFrames
    for method, df in aggregated_results.items():
        print(f"Aggregated results for {method}:\n", df)
        df.to_csv(os.path.join(paths.results_base_path, f'{method}_fold_report_results.csv'))

    # Compute and save average scores across all folds (or the single split)
    for method in settings.method_list:
        for metric in settings.metric_list:
            avg_score = np.mean([result[metric] for result in fold_results[method]])
            std_score = np.std([result[metric] for result in fold_results[method]])
            results_logger.update_result(method, metric, avg_score, std_score)
            print(f"Method {method}: {metric}: {avg_score} ± {std_score}")

    # Save overall results to CSV
    result_df = results_logger.to_dataframe()
    result_df.to_csv(os.path.join(paths.base_path, paths.folder_name, f'{settings.cross_validation_mode}_results.csv'))
    
    all_results.append(result_df)
all_results_df = pd.concat(all_results)
all_results_df.to_csv(os.path.join(paths.base_path, paths.folder_name, f'{settings.cross_validation_mode}_results.csv'))


====== Subject 0 (p05_task1_block2_CLEAR_S2_flicker) ====== 

Creating path D:\projects\Neural_Signal_Classifier/results//flicker/2024-09-20-17-19-52/p05_task1_block2_CLEAR_S2_latent_dim_1/ ...
=========== Train Subject 1 Fold 1 Model ldgd Latent dim 1 =========== 



 D:\projects\Neural_Signal_Classifier\src\model\model_ldgd.py:39: UserWarning:To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).
 C:\Users\Navid Ziaei\.conda\envs\pytorch\Lib\site-packages\linear_operator\utils\interpolation.py:71: UserWarning:The torch.cuda.*DtypeTensor constructors are no longer recommended. It's best to use methods such as torch.tensor(data, dtype=*, device='cuda') to create tensors. (Triggered internally at ..\torch\csrc\tensor\python_tensor.cpp:80.)
 C:\Users\Navid Ziaei\.conda\envs\pytorch\Lib\site-packages\linear_operator\utils\interpolation.py:71: UserWarning:torch.sparse.SparseTensor(indices, values, shape, *, device=) is deprecated.  Please use torch.sparse_coo_tensor(indices, values, shape, dtype=, device=). (Triggered internally at ..\torch\csrc\utils\tensor_new.cpp:623.)


model saved!
Epoch 1/1500, Loss: 2.268171548843384, Accuracy: 0.6875
Epoch 11/1500, Loss: 2.020801305770874, Accuracy: 0.6125
Epoch 21/1500, Loss: 1.8311742544174194, Accuracy: 0.6625
model saved!
Epoch 31/1500, Loss: 1.7055447101593018, Accuracy: 0.7125
model saved!
Epoch 41/1500, Loss: 1.5347846746444702, Accuracy: 0.7375
model saved!
Epoch 51/1500, Loss: 1.454373836517334, Accuracy: 0.775
model saved!
Epoch 61/1500, Loss: 1.319338083267212, Accuracy: 0.8625
model saved!
Epoch 71/1500, Loss: 1.1746776103973389, Accuracy: 0.875
model saved!
Epoch 81/1500, Loss: 1.1065958738327026, Accuracy: 0.9
model saved!
Epoch 91/1500, Loss: 1.020786166191101, Accuracy: 0.925
model saved!
Epoch 101/1500, Loss: 0.9210139513015747, Accuracy: 0.925
model saved!
Epoch 111/1500, Loss: 0.8021756410598755, Accuracy: 0.9375
model saved!
Epoch 121/1500, Loss: 0.7539471983909607, Accuracy: 0.9375
model saved!
Epoch 131/1500, Loss: 0.7318549752235413, Accuracy: 0.95
model saved!
Epoch 141/1500, Loss: 0.633505

 D:\projects\Neural_Signal_Classifier\src\model\model_ldgd.py:39: UserWarning:To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).


Epoch 11/1500, Loss: 2.046076536178589, Accuracy: 0.4875
Epoch 21/1500, Loss: 1.8678443431854248, Accuracy: 0.5
model saved!
Epoch 31/1500, Loss: 1.706621527671814, Accuracy: 0.525
model saved!
Epoch 41/1500, Loss: 1.597689151763916, Accuracy: 0.5375
model saved!
Epoch 51/1500, Loss: 1.527616024017334, Accuracy: 0.5375
model saved!
Epoch 61/1500, Loss: 1.39594566822052, Accuracy: 0.625
model saved!
Epoch 71/1500, Loss: 1.3468512296676636, Accuracy: 0.675
model saved!
Epoch 81/1500, Loss: 1.2378836870193481, Accuracy: 0.7
model saved!
Epoch 91/1500, Loss: 1.1490707397460938, Accuracy: 0.775
model saved!
Epoch 101/1500, Loss: 1.0636932849884033, Accuracy: 0.7875
model saved!
Epoch 111/1500, Loss: 0.9817326068878174, Accuracy: 0.8375
model saved!
Epoch 121/1500, Loss: 0.8667088150978088, Accuracy: 0.8625
model saved!
Epoch 131/1500, Loss: 0.8006871938705444, Accuracy: 0.9
model saved!
Epoch 141/1500, Loss: 0.699686586856842, Accuracy: 0.9
Epoch 151/1500, Loss: 0.7437819838523865, Accuracy

...

 D:\projects\Neural_Signal_Classifier\src\model\model_ldgd.py:39: UserWarning:To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).


Epoch 11/1500, Loss: 2.288156270980835, Accuracy: 0.5
model saved!
Epoch 21/1500, Loss: 2.230592727661133, Accuracy: 0.5625
Epoch 31/1500, Loss: 2.1786246299743652, Accuracy: 0.5
Epoch 41/1500, Loss: 2.1299755573272705, Accuracy: 0.525
model saved!
Epoch 51/1500, Loss: 2.0818889141082764, Accuracy: 0.5625
Epoch 61/1500, Loss: 2.033879518508911, Accuracy: 0.4875
Epoch 71/1500, Loss: 1.9747741222381592, Accuracy: 0.4875
Epoch 81/1500, Loss: 1.9042599201202393, Accuracy: 0.5
Epoch 91/1500, Loss: 1.8337651491165161, Accuracy: 0.5
Epoch 101/1500, Loss: 1.7479091882705688, Accuracy: 0.4875
Epoch 111/1500, Loss: 1.6661465167999268, Accuracy: 0.5125
Epoch 121/1500, Loss: 1.5601253509521484, Accuracy: 0.525
Epoch 131/1500, Loss: 1.4701381921768188, Accuracy: 0.5
Epoch 141/1500, Loss: 1.3517409563064575, Accuracy: 0.5
Epoch 151/1500, Loss: 1.274453043937683, Accuracy: 0.5
Epoch 161/1500, Loss: 1.1799886226654053, Accuracy: 0.5
Epoch 171/1500, Loss: 1.1201140880584717, Accuracy: 0.5125
Epoch 181/

 C:\Users\Navid Ziaei\.conda\envs\pytorch\Lib\site-packages\LDGD\visualization\vizualize_utils.py:328: UserWarning:The following kwargs were not used by contour: 'label'


Aggregated results for ldgd:
               precision_mean  precision_std  recall_mean  recall_std  \
0.0                 0.844402       0.050033         0.82    0.097980   
1.0                 0.837273       0.085106         0.84    0.080000   
accuracy                 NaN            NaN          NaN         NaN   
macro avg           0.840837       0.030691         0.83    0.024495   
weighted avg        0.840837       0.030691         0.83    0.024495   

              f1-score_mean  f1-score_std  support_mean  support_std  
0.0                0.826311      0.032917          10.0          0.0  
1.0                0.831199      0.022574          10.0          0.0  
accuracy                NaN           NaN           NaN          NaN  
macro avg          0.828755      0.024337          20.0          0.0  
weighted avg       0.828755      0.024337          20.0          0.0  
Method ldgd: accuracy: 0.8299999999999998 ± 0.024494897427831747
Method ldgd: f1_score: 0.8287550465717108 ± 0.

 C:\Users\Navid Ziaei\.conda\envs\pytorch\Lib\site-packages\numpy\core\fromnumeric.py:3504: RuntimeWarning:Mean of empty slice.
 C:\Users\Navid Ziaei\.conda\envs\pytorch\Lib\site-packages\numpy\core\_methods.py:129: RuntimeWarning:invalid value encountered in scalar divide
 C:\Users\Navid Ziaei\.conda\envs\pytorch\Lib\site-packages\numpy\core\_methods.py:206: RuntimeWarning:Degrees of freedom <= 0 for slice
 C:\Users\Navid Ziaei\.conda\envs\pytorch\Lib\site-packages\numpy\core\_methods.py:163: RuntimeWarning:invalid value encountered in divide
 C:\Users\Navid Ziaei\.conda\envs\pytorch\Lib\site-packages\numpy\core\_methods.py:198: RuntimeWarning:invalid value encountered in scalar divide


In [8]:
# Perform training with cross-validation or single fold

random_seed = 42
patient_id = 0
patient_file_name_base = list(features_raw_df_dict.keys())[1]
features_df = features_raw_df_dict[patient_file_name_base]

print(f"====== Subject {patient_id} ({patient_file_name_base.split('.')[0]}) ====== \n")
# Extract labels and features
y_one_hot, labels_array, unique_pids, patients_files, features_df, target_columns = get_labels(features_df,
                                                                                               settings)
if settings.cross_validation_mode in ['k-fold', 'order']:
    # Generate k-folds for cross-validation
    cv_mode = setup_cross_validation(settings.cross_validation_mode, num_folds=settings.num_fold,
                                     random_state=random_seed)
    folds = generate_folds(features_df, labels_array, cv_mode, n_splits=settings.num_fold)
    folds = list(folds)
else:  # Single train/test split
    folds = [(train_test_split(np.arange(len(labels_array)), test_size=0.2, stratify=labels_array))]
        
all_results = []
for num_inducing_points in [2, 5, 7, 10, 25]:
    for latent_dim in [1, 2, 3, 5, 7, 10]:
        patient_id = patient_id + 1
        settings.ldgd_configs['latent_dim'] = latent_dim
        settings.ldgd_configs['num_inducing_points'] = num_inducing_points

        # settings.num_epochs_train = num_epochs_train
        results_logger = ResultList(method_list=settings.method_list, metric_list=settings.metric_list)
    
        results_logger.add_subject(unique_pids=patient_id, patients_files=patients_files, params=f'_latent_dim_{latent_dim}_inducing_{num_inducing_points}')
        paths.create_subject_paths(patients_files.split('.')[0]+f'_latent_dim_{latent_dim}_inducing_{num_inducing_points}')
            
        fold_results = {method: [] for method in settings.method_list}
        fold_report_results = {method: [] for method in settings.method_list}
    
        for fold_idx, (train_index, test_index) in enumerate(folds):
            paths.create_fold_path(fold_idx)
    
            # Select features and prepare the training and testing datasets
            features_matrix, selected_features, patients_ids, _ = get_selected_features(
                features_df=features_df.copy(), settings=settings, paths=paths,
                fold_idx=fold_idx, train_index=train_index, target_columns_drop=get_drop_columns(settings),
                num_important_features=settings.num_important_features)
    
            data_train, data_test = features_matrix[train_index], features_matrix[test_index]
            labels_train, labels_test = labels_array[train_index], labels_array[test_index]
            y_train, y_test = y_one_hot[train_index], y_one_hot[test_index]
    
            # Train and evaluate models for each specified method
            for method in settings.method_list:
                print(f"=========== Train Subject {patient_id} Fold {fold_idx + 1} Model {method} Latent dim {latent_dim} =========== \n")
                results, report_results = train_model(method,
                                                      data_train=data_train,
                                                      labels_train=labels_train,
                                                      data_test=data_test,
                                                      labels_test=labels_test,
                                                      settings=settings,
                                                      paths=paths,
                                                      y_train=y_train,
                                                      y_test=y_test,
                                                      selected_features=selected_features,
                                                      target_columns=target_columns)
                fold_results[method].append(results)
                fold_report_results[method].append(report_results)
    
            plt.close('all')
        
        # Aggregate the results for fold reports
        aggregated_results = aggregate_fold_report_results(fold_report_results)
    
    
        # Save or print the DataFrames
        for method, df in aggregated_results.items():
            print(f"Aggregated results for {method}:\n", df)
            df.to_csv(os.path.join(paths.results_base_path, f'{method}_fold_report_results.csv'))
    
        # Compute and save average scores across all folds (or the single split)
        for method in settings.method_list:
            for metric in settings.metric_list:
                avg_score = np.mean([result[metric] for result in fold_results[method]])
                std_score = np.std([result[metric] for result in fold_results[method]])
                results_logger.update_result(method, metric, avg_score, std_score)
                print(f"Method {method}: {metric}: {avg_score} ± {std_score}")
    
        # Save overall results to CSV
        result_df = results_logger.to_dataframe()
        result_df.to_csv(os.path.join(paths.base_path, paths.folder_name, f'{settings.cross_validation_mode}_results.csv'))
        
        all_results.append(result_df)
all_results_df = pd.concat(all_results)
all_results_df.to_csv(os.path.join(paths.base_path, paths.folder_name, f'{settings.cross_validation_mode}_results.csv'))
 

====== Subject 0 (p05_task1_block2_CLEAR_S2_flicker) ====== 

Creating path D:\projects\Neural_Signal_Classifier/results//flicker/2024-09-20-17-19-52/p05_task1_block2_CLEAR_S2_latent_dim_1_inducing_2/ ...
=========== Train Subject 1 Fold 1 Model ldgd Latent dim 1 =========== 



 D:\projects\Neural_Signal_Classifier\src\model\model_ldgd.py:39: UserWarning:To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).


model saved!
Epoch 1/1500, Loss: 2.2681522369384766, Accuracy: 0.5375
Epoch 11/1500, Loss: 2.10752272605896, Accuracy: 0.525
Epoch 21/1500, Loss: 1.9685741662979126, Accuracy: 0.525
Epoch 31/1500, Loss: 1.8482246398925781, Accuracy: 0.525
model saved!
Epoch 41/1500, Loss: 1.7096707820892334, Accuracy: 0.575
model saved!
Epoch 51/1500, Loss: 1.5912625789642334, Accuracy: 0.675
model saved!
Epoch 61/1500, Loss: 1.469177484512329, Accuracy: 0.7
model saved!
Epoch 71/1500, Loss: 1.3466006517410278, Accuracy: 0.7625
model saved!
Epoch 81/1500, Loss: 1.2803419828414917, Accuracy: 0.8
model saved!
Epoch 91/1500, Loss: 1.1423125267028809, Accuracy: 0.875
model saved!
Epoch 101/1500, Loss: 1.0687556266784668, Accuracy: 0.9
model saved!
Epoch 111/1500, Loss: 1.0091785192489624, Accuracy: 0.925
model saved!
Epoch 121/1500, Loss: 0.8751448392868042, Accuracy: 0.925
model saved!
Epoch 131/1500, Loss: 0.7808465361595154, Accuracy: 0.9375
model saved!
Epoch 141/1500, Loss: 0.6587928533554077, Accurac

 D:\projects\Neural_Signal_Classifier\src\model\model_ldgd.py:39: UserWarning:To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).


model saved!
Epoch 11/1500, Loss: 2.1250178813934326, Accuracy: 0.5625
model saved!
Epoch 21/1500, Loss: 1.9834247827529907, Accuracy: 0.5875
model saved!
Epoch 31/1500, Loss: 1.8477997779846191, Accuracy: 0.625
model saved!
Epoch 41/1500, Loss: 1.7279235124588013, Accuracy: 0.65
model saved!
Epoch 51/1500, Loss: 1.6008111238479614, Accuracy: 0.675
model saved!
Epoch 61/1500, Loss: 1.5300511121749878, Accuracy: 0.7125
model saved!
Epoch 71/1500, Loss: 1.4288398027420044, Accuracy: 0.725
model saved!
Epoch 81/1500, Loss: 1.3162603378295898, Accuracy: 0.7375
model saved!
Epoch 91/1500, Loss: 1.2777739763259888, Accuracy: 0.775
model saved!
Epoch 101/1500, Loss: 1.1388702392578125, Accuracy: 0.825
model saved!
Epoch 111/1500, Loss: 1.0089545249938965, Accuracy: 0.85
model saved!
Epoch 121/1500, Loss: 0.9491084814071655, Accuracy: 0.875
model saved!
Epoch 131/1500, Loss: 0.8895555734634399, Accuracy: 0.9
model saved!
Epoch 141/1500, Loss: 0.7319012880325317, Accuracy: 0.925
model saved!
Ep

...

 D:\projects\Neural_Signal_Classifier\src\model\model_ldgd.py:39: UserWarning:To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).


model saved!
Epoch 1/1500, Loss: 2.3502755165100098, Accuracy: 0.525
model saved!
Epoch 11/1500, Loss: 2.283566474914551, Accuracy: 0.5375
Epoch 21/1500, Loss: 2.2263734340667725, Accuracy: 0.4875
model saved!
Epoch 31/1500, Loss: 2.1746222972869873, Accuracy: 0.55
model saved!
Epoch 41/1500, Loss: 2.1260499954223633, Accuracy: 0.6
Epoch 51/1500, Loss: 2.0758090019226074, Accuracy: 0.5625
Epoch 61/1500, Loss: 2.019608974456787, Accuracy: 0.55
Epoch 71/1500, Loss: 1.9565600156784058, Accuracy: 0.525
Epoch 81/1500, Loss: 1.8868767023086548, Accuracy: 0.5125
Epoch 91/1500, Loss: 1.7995359897613525, Accuracy: 0.525
Epoch 101/1500, Loss: 1.7110719680786133, Accuracy: 0.4875
Epoch 111/1500, Loss: 1.5948066711425781, Accuracy: 0.5
Epoch 121/1500, Loss: 1.484144687652588, Accuracy: 0.5
Epoch 131/1500, Loss: 1.3742467164993286, Accuracy: 0.5
Epoch 141/1500, Loss: 1.2595901489257812, Accuracy: 0.5375
model saved!
Epoch 151/1500, Loss: 1.1724097728729248, Accuracy: 0.7375
model saved!
Epoch 161/1

 C:\Users\Navid Ziaei\.conda\envs\pytorch\Lib\site-packages\LDGD\visualization\vizualize_utils.py:328: UserWarning:The following kwargs were not used by contour: 'label'


Aggregated results for ldgd:
               precision_mean  precision_std  recall_mean  recall_std  \
0.0                 0.816624       0.055841         0.78    0.132665   
1.0                 0.806970       0.109878         0.82    0.074833   
accuracy                 NaN            NaN          NaN         NaN   
macro avg           0.811797       0.059815         0.80    0.054772   
weighted avg        0.811797       0.059815         0.80    0.054772   

              f1-score_mean  f1-score_std  support_mean  support_std  
0.0                0.791223      0.069998          10.0          0.0  
1.0                0.805225      0.043133          10.0          0.0  
accuracy                NaN           NaN           NaN          NaN  
macro avg          0.798224      0.055196          20.0          0.0  
weighted avg       0.798224      0.055196          20.0          0.0  
Method ldgd: accuracy: 0.8 ± 0.05477225575051662
Method ldgd: f1_score: 0.7982241739355752 ± 0.0551955733875370

 C:\Users\Navid Ziaei\.conda\envs\pytorch\Lib\site-packages\numpy\core\fromnumeric.py:3504: RuntimeWarning:Mean of empty slice.
 C:\Users\Navid Ziaei\.conda\envs\pytorch\Lib\site-packages\numpy\core\_methods.py:129: RuntimeWarning:invalid value encountered in scalar divide
 C:\Users\Navid Ziaei\.conda\envs\pytorch\Lib\site-packages\numpy\core\_methods.py:206: RuntimeWarning:Degrees of freedom <= 0 for slice
 C:\Users\Navid Ziaei\.conda\envs\pytorch\Lib\site-packages\numpy\core\_methods.py:163: RuntimeWarning:invalid value encountered in divide
 C:\Users\Navid Ziaei\.conda\envs\pytorch\Lib\site-packages\numpy\core\_methods.py:198: RuntimeWarning:invalid value encountered in scalar divide


In [9]:
all_results_df

subject id                                           filename  \
0           1  p05_task1_block2_CLEAR_S2_latent_dim_1_inducing_2   
0           2  p05_task1_block2_CLEAR_S2_latent_dim_2_inducing_2   
0           3  p05_task1_block2_CLEAR_S2_latent_dim_3_inducing_2   
0           4  p05_task1_block2_CLEAR_S2_latent_dim_5_inducing_2   
0           5  p05_task1_block2_CLEAR_S2_latent_dim_7_inducing_2   
0           6  p05_task1_block2_CLEAR_S2_latent_dim_10_induci...   
0           7  p05_task1_block2_CLEAR_S2_latent_dim_1_inducing_5   
0           8  p05_task1_block2_CLEAR_S2_latent_dim_2_inducing_5   
0           9  p05_task1_block2_CLEAR_S2_latent_dim_3_inducing_5   
0          10  p05_task1_block2_CLEAR_S2_latent_dim_5_inducing_5   
0          11  p05_task1_block2_CLEAR_S2_latent_dim_7_inducing_5   
0          12  p05_task1_block2_CLEAR_S2_latent_dim_10_induci...   
0          13  p05_task1_block2_CLEAR_S2_latent_dim_1_inducing_7   
0          14  p05_task1_block2_CLEAR_S2_latent_dim_2_inducing_7   
0          15  p05_task1_block2_CLEAR_S2_latent_dim_3_inducing_7   
0          16  p05_task1_block2_CLEAR_S2_latent_dim_5_inducing_7   
0          17  p05_task1_block2_CLEAR_S2_latent_dim_7_inducing_7   
0          18  p05_task1_block2_CLEAR_S2_latent_dim_10_induci...   
0          19  p05_task1_block2_CLEAR_S2_latent_dim_1_inducin...   
0          20  p05_task1_block2_CLEAR_S2_latent_dim_2_inducin...   
0          21  p05_task1_block2_CLEAR_S2_latent_dim_3_inducin...   
0          22  p05_task1_block2_CLEAR_S2_latent_dim_5_inducin...   
0          23  p05_task1_block2_CLEAR_S2_latent_dim_7_inducin...   
0          24  p05_task1_block2_CLEAR_S2_latent_dim_10_induci...   
0          25  p05_task1_block2_CLEAR_S2_latent_dim_1_inducin...   
0          26  p05_task1_block2_CLEAR_S2_latent_dim_2_inducin...   
0          27  p05_task1_block2_CLEAR_S2_latent_dim_3_inducin...   
0          28  p05_task1_block2_CLEAR_S2_latent_dim_5_inducin...   
0          29  p05_task1_block2_CLEAR_S2_latent_dim_7_inducin...   
0          30  p05_task1_block2_CLEAR_S2_latent_dim_10_induci...   

   ldgd avg_accuracy  ldgd std_accuracy  ldgd avg_f1_score  ldgd std_f1_score  \
0               0.84           0.073485           0.838183           0.074572   
0               0.86           0.058310           0.857829           0.060461   
0               0.85           0.089443           0.848208           0.090568   
0               0.80           0.031623           0.794521           0.036961   
0               0.79           0.101980           0.779942           0.116545   
0               0.69           0.139284           0.632594           0.207401   
0               0.80           0.083666           0.798941           0.084303   
0               0.80           0.044721           0.798984           0.044159   
0               0.81           0.037417           0.807275           0.038681   
0               0.80           0.044721           0.797958           0.045343   
0               0.84           0.048990           0.838418           0.048947   
0               0.83           0.024495           0.828140           0.023836   
0               0.83           0.050990           0.827477           0.052471   
0               0.79           0.058310           0.786836           0.058328   
0               0.83           0.060000           0.829269           0.060138   
0               0.84           0.048990           0.839447           0.048927   
0               0.80           0.031623           0.798376           0.030740   
0               0.82           0.050990           0.818578           0.050610   
0               0.82           0.081240           0.818370           0.081831   
0               0.83           0.067823           0.829472           0.067889   
0               0.82           0.050990           0.818168           0.052391   
0               0.83           0.050990           0.829118           0.051092   
0               0.85           

In [ ]:
paths.results_base_path
